# News Modeling

Topic modeling involves **extracting features from document terms** and using
mathematical structures and frameworks like matrix factorization and SVD to generate **clusters or groups of terms** that are distinguishable from each other and these clusters of words form topics or concepts

Topic modeling is a method for **unsupervised classification** of documents, similar to clustering on numeric data

These concepts can be used to interpret the main **themes** of a corpus and also make **semantic connections among words that co-occur together** frequently in various documents

Topic modeling can help in the following areas:
- discovering the **hidden themes** in the collection
- **classifying** the documents into the discovered themes
- using the classification to **organize/summarize/search** the documents

Frameworks and algorithms to build topic models:
- Latent semantic indexing
- Latent Dirichlet allocation
- Non-negative matrix factorization

## Latent Dirichlet Allocation (LDA)
The latent Dirichlet allocation (LDA) technique is a **generative probabilistic model** where each **document is assumed to have a combination of topics** similar to a probabilistic latent semantic indexing model

In simple words, the idea behind LDA is that of two folds:
- each **document** can be described by a **distribution of topics**
- each **topic** can be described by a **distribution of words**

### LDA Algorithm

- 1. For each document, **randomly initialize each word to one of the K topics** (k is chosen beforehand)
- 2. For each document D, go through each word w and compute:
    - **P(T |D)** , which is a proportion of words in D assigned to topic T
    - **P(W |T )** , which is a proportion of assignments to topic T over all documents having the word W
- **Reassign word W with topic T** with probability P(T |D)´ P(W |T ) considering all other words and their topic assignments

![LDA](https://raw.githubusercontent.com/subashgandyer/datasets/main/images/LDA.png)

### Steps
- Install the necessary library
- Import the necessary libraries
- Download the dataset
- Load the dataset
- Pre-process the dataset
    - Stop words removal
    - Email removal
    - Non-alphabetic words removal
    - Tokenize
    - Lowercase
    - BiGrams & TriGrams
    - Lemmatization
- Create a dictionary for the document
- Filter low frequency words
- Create an Index to word dictionary
- Train the Topic Model
- Predict on the dataset
- Evaluate the Topic Model
    - Model Perplexity
    - Topic Coherence
- Visualize the topics

### Install the necessary library

In [1]:
#! pip install pyLDAvis gensim spacy

Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 2.6 MB 5.4 MB/s eta 0:00:01
     |████████████████████████████████| 102 kB 19.7 MB/s eta 0:00:01
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


### Import the libraries

In [60]:
import gensim
import spacy
import pandas as pd
from gensim.utils import simple_preprocess
from gensim.models.phrases import Phrases, Phraser
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis



### Download the dataset
Dataset: https://raw.githubusercontent.com/subashgandyer/datasets/main/newsgroups.json

#### 20-Newsgroups dataset
- 11K newsgroups posts
- 20 news topics

In [15]:
import requests

url = "https://raw.githubusercontent.com/subashgandyer/datasets/main/newsgroups.json"
data = requests.get(url).json()

### Load the dataset

In [26]:
df = pd.DataFrame(data)
df

content  target  \
0      From: lerxst@wam.umd.edu (where's my thing)\nS...       7   
1      From: guykuo@carson.u.washington.edu (Guy Kuo)...       4   
2      From: twillis@ec.ecn.purdue.edu (Thomas E Will...       4   
3      From: jgreen@amber (Joe Green)\nSubject: Re: W...       1   
4      From: jcm@head-cfa.harvard.edu (Jonathan McDow...      14   
...                                                  ...     ...   
11309  From: jim.zisfein@factory.com (Jim Zisfein) \n...      13   
11310  From: ebodin@pearl.tufts.edu\nSubject: Screen ...       4   
11311  From: westes@netcom.com (Will Estes)\nSubject:...       3   
11312  From: steve@hcrlgw (Steven Collins)\nSubject: ...       1   
11313  From: gunning@cco.caltech.edu (Kevin J. Gunnin...       8   

                   target_names  
0                     rec.autos  
1         comp.sys.mac.hardware  
2         comp.sys.mac.hardware  
3                 comp.graphics  
4                     sci.space  
...                         ...  
11309                   sci.med  
11310     comp.sys.mac.hardware  
11311  comp.sys.ibm.pc.hardware  
11312             comp.graphics  
11313           rec.motorcycles  

[11314 rows x 3 columns]

### Preprocess the data

### Email Removal

In [27]:
import re

In [28]:
df['content'] = df['content'].apply(lambda x: re.sub(r'\S*@\S*\s?', '', x))

### Newline Removal

In [30]:
df['content'] = df['content'].replace('\n', ' ', regex=True)

### Single Quotes Removal

In [32]:
df['content'] = df['content'].replace("'", "", regex=True)

### Tokenize
- Create **sent_to_words()** 
    - Use **gensim.utils.simple_preprocess**
    - Use **generator** instead of an usual function

In [36]:
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))

In [35]:
data_words = list(sent_to_words(df['content']))

### Stop words Removal
- Extend the stop words corpus with the following words
    - from
    - subject
    - re
    - edu
    - use

In [38]:
from gensim.parsing.preprocessing import STOPWORDS

my_stop_words = STOPWORDS.union(set(['from', 'subject', 're', 'edu', 'use']))

#### remove_stopwords( )

In [39]:
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in my_stop_words] for doc in texts]

In [40]:
data_words_nostops = remove_stopwords(data_words)

In [41]:
data_words_nostops

[['wheres',
  'thing',
  'car',
  'nntp',
  'posting',
  'host',
  'rac',
  'wam',
  'umd',
  'organization',
  'university',
  'maryland',
  'college',
  'park',
  'lines',
  'wondering',
  'enlighten',
  'car',
  'saw',
  'day',
  'door',
  'sports',
  'car',
  'looked',
  'late',
  'early',
  'called',
  'bricklin',
  'doors',
  'small',
  'addition',
  'bumper',
  'separate',
  'rest',
  'body',
  'know',
  'tellme',
  'model',
  'engine',
  'specs',
  'years',
  'production',
  'car',
  'history',
  'info',
  'funky',
  'looking',
  'car',
  'mail',
  'thanks',
  'il',
  'brought',
  'neighborhood',
  'lerxst'],
 ['guy',
  'kuo',
  'si',
  'clock',
  'poll',
  'final',
  'summary',
  'final',
  'si',
  'clock',
  'reports',
  'keywords',
  'si',
  'acceleration',
  'clock',
  'upgrade',
  'article',
  'shelley',
  'qvfo',
  'innc',
  'organization',
  'university',
  'washington',
  'lines',
  'nntp',
  'posting',
  'host',
  'carson',
  'washington',
  'fair',
  'number',
  'brav

### Bigrams
- Use **gensim.models.Phrases**
- 100 as threshold

In [42]:
bigram = gensim.models.Phrases(data_words, min_count=5, threshold=100)
bigram_mod = gensim.models.phrases.Phraser(bigram)


#### make_bigrams( )

In [43]:
def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]

In [44]:
data_words_bigrams = make_bigrams(data_words_nostops)

In [45]:
data_words_bigrams

[['wheres',
  'thing',
  'car',
  'nntp_posting',
  'host',
  'rac_wam',
  'umd',
  'organization',
  'university',
  'maryland_college',
  'park',
  'lines',
  'wondering',
  'enlighten',
  'car',
  'saw',
  'day',
  'door',
  'sports',
  'car',
  'looked',
  'late',
  'early',
  'called',
  'bricklin',
  'doors',
  'small',
  'addition',
  'bumper',
  'separate',
  'rest',
  'body',
  'know',
  'tellme',
  'model',
  'engine',
  'specs',
  'years',
  'production',
  'car',
  'history',
  'info',
  'funky',
  'looking',
  'car',
  'mail',
  'thanks',
  'il',
  'brought',
  'neighborhood',
  'lerxst'],
 ['guy_kuo',
  'si',
  'clock',
  'poll',
  'final',
  'summary',
  'final',
  'si',
  'clock',
  'reports',
  'keywords',
  'si',
  'acceleration',
  'clock',
  'upgrade',
  'article',
  'shelley',
  'qvfo',
  'innc',
  'organization',
  'university',
  'washington',
  'lines',
  'nntp_posting',
  'host',
  'carson_washington',
  'fair',
  'number',
  'brave',
  'souls',
  'upgraded',
 

['from', 'wheres', 'my', 'thing', 'subject', 'what', 'car', 'is', 'this', 'nntp_posting_host', 'rac_wam_umd_edu', 'organization', 'university', 'of', 'maryland_college_park', 'lines', 'was', 'wondering', 'if', 'anyone', 'out', 'there', 'could', 'enlighten', 'me', 'on', 'this', 'car', 'saw', 'the', 'other', 'day', 'it', 'was', 'door', 'sports', 'car', 'looked', 'to', 'be', 'from', 'the', 'late', 'early', 'it', 'was', 'called', 'bricklin', 'the', 'doors', 'were', 'really', 'small', 'in', 'addition', 'the', 'front_bumper', 'was', 'separate', 'from', 'the', 'rest', 'of', 'the', 'body', 'this', 'is', 'all', 'know', 'if', 'anyone', 'can', 'tellme', 'model', 'name', 'engine', 'specs', 'years', 'of', 'production', 'where', 'this', 'car', 'is', 'made', 'history', 'or', 'whatever', 'info', 'you', 'have', 'on', 'this', 'funky', 'looking', 'car', 'please', 'mail', 'thanks', 'il', 'brought', 'to', 'you', 'by', 'your', 'neighborhood', 'lerxst']


/Users/subashgandyer/.local/lib/python3.8/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


### Lemmatization
- Use spacy
    - Download spacy en model (if you have not done that before)
    - Load the spacy model

In [20]:
#! python -m spacy download en

/Users/subashgandyer/.local/lib/python3.8/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [48]:
# nlp = spacy.load('en', disable=['parser', 'ner'])
nlp = spacy.load('en_core_web_sm', disable=['parser', 'ner'])

#### lemmatizaton( )

In [49]:
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [50]:
data_lemmatized = lemmatization(data_words_bigrams, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])

In [51]:
print(data_lemmatized[:1])

[['s', 'thing', 'car', 'nntp_poste', 'host', 'rac_wam', 'university', 'park', 'line', 'wonder', 'enlighten', 'car', 'see', 'day', 'door', 'sport', 'car', 'look', 'late', 'early', 'call', 'door', 'small', 'addition', 'bumper', 'separate', 'rest', 'body', 'know', 'model', 'engine', 'spec', 'year', 'production', 'car', 'history', 'info', 'funky', 'look', 'car', 'mail', 'thank', 'bring', 'neighborhood', 'lerxst']]


### Create a Dictionary

In [52]:
id2word = gensim.corpora.Dictionary(data_lemmatized)

### Create Corpus

In [53]:
texts = data_lemmatized
corpus = [id2word.doc2bow(text) for text in texts]


### Filter low-frequency words

In [54]:
id2word.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)


### Create Index 2 word dictionary

In [55]:
id2word = gensim.corpora.Dictionary(data_lemmatized)


### Build a News Topic Model

#### LdaModel
- **num_topics** : this is the number of topics you need to define beforehand
- **chunksize** : the number of documents to be used in each training chunk
- **alpha** : this is the hyperparameters that affect the sparsity of the topics
- **passess** : total number of training assess

In [56]:
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=20,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)


### Print the Keyword in the 10 topics

In [57]:
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))


Topic: 0 
Words: 0.107*"team" + 0.099*"game" + 0.085*"win" + 0.074*"play" + 0.043*"year" + 0.034*"server" + 0.028*"run" + 0.026*"goal" + 0.025*"score" + 0.021*"division"
Topic: 1 
Words: 0.063*"wing" + 0.062*"nhl" + 0.057*"controller" + 0.047*"external" + 0.039*"vote" + 0.033*"flight" + 0.032*"hook" + 0.032*"battery" + 0.024*"percent" + 0.023*"task"
Topic: 2 
Words: 0.124*"gun" + 0.054*"law" + 0.042*"crime" + 0.040*"weapon" + 0.039*"citizen" + 0.032*"firearm" + 0.025*"rate" + 0.023*"tax" + 0.022*"court" + 0.019*"carry"
Topic: 3 
Words: 0.051*"character" + 0.043*"monitor" + 0.041*"internal" + 0.030*"series" + 0.029*"cable" + 0.029*"hole" + 0.028*"normal" + 0.028*"generate" + 0.027*"past" + 0.024*"font"
Topic: 4 
Words: 0.051*"sale" + 0.042*"player" + 0.033*"cheap" + 0.033*"bike" + 0.027*"wire" + 0.027*"drug" + 0.022*"review" + 0.019*"ride" + 0.018*"ground" + 0.018*"material"
Topic: 5 
Words: 0.057*"evidence" + 0.037*"believe" + 0.032*"reason" + 0.029*"faith" + 0.024*"sense" + 0.022*"exi

## Evaluation of Topic Models
- Model Perplexity
- Topic Coherence

### Model Perplexity

Model perplexity is a measurement of **how well** a **probability distribution** or probability model **predicts a sample**

In [58]:
print('Perplexity: ', lda_model.log_perplexity(corpus))

Perplexity:  -13.822208537623625


### Topic Coherence
Topic Coherence measures score a single topic by measuring the **degree of semantic similarity** between **high scoring words** in the topic.

In [59]:
from gensim.models import CoherenceModel

coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('Coherence Score: ', coherence_lda)

/Users/admin/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2.0 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
/Users/admin/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2.0 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
/Users/admin/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2.0 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
/Users/admin/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2.0 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compi

Coherence Score:  0.5348419123535703


### Visualize the Topic Model
- Use **pyLDAvis**
    - designed to help users **interpret the topics** in a topic model that has been fit to a corpus of text data
    - extracts information from a fitted LDA topic model to inform an interactive web-based visualization

In [61]:
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, id2word)
vis

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
19     0.359455  0.048055       1        1  34.841649
13     0.350288  0.158163       2        1  21.532903
11     0.311299 -0.162455       3        1  13.822398
18    -0.018120 -0.061817       4        1   5.880107
17     0.088544 -0.208684       5        1   4.181338
5      0.171546  0.240222       6        1   3.331987
8      0.036944 -0.241505       7        1   2.470247
4     -0.025455 -0.064616       8        1   2.288912
0     -0.014798 -0.008698       9        1   1.750548
16    -0.062788  0.001840      10        1   1.710847
6     -0.064618  0.047965      11        1   1.328195
14    -0.070448 -0.053069      12        1   1.249922
2     -0.090058  0.034113      13        1   1.034519
3     -0.126743  0.025564      14        1   0.966612
12    -0.094432  0.067774      15        1   0.920605
15    -0.120250  0.030027      16        1   0.755689
10    -0.143162  0.049682      17        1   0.604443
1     -0.150078  0.030399      18        1   0.528454
9     -0.160218  0.031575      19        1   0.483062
7     -0.176909  0.035467      20        1   0.317564, topic_info=          Term          Freq         Total Category  logprob  loglift
4279        ax  55332.000000  55332.000000  Default  30.0000  30.0000
197      write  14505.000000  14505.000000  Default  29.0000  29.0000
18        line  18629.000000  18629.000000  Default  28.0000  28.0000
38        year   5130.000000   5130.000000  Default  27.0000  27.0000
135     people   8381.000000   8381.000000  Default  26.0000  26.0000
...        ...           ...           ...      ...      ...      ...
1428  escalate      7.314663      8.616841  Topic20  -6.2330   5.5884
1423    cradle      6.709527      8.011705  Topic20  -6.3194   5.5749
1883     viola      3.526430      4.828608  Topic20  -6.9626   5.4380
1435  ointment      2.815825      4.118003  Topic20  -7.1877   5.3721
1439     scalp      0.291430      1.593608  Topic20  -9.4559   4.0533

[837 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
459       6  0.992832   absolute
3203     19  0.956872   abstract
1299      1  0.282474     accept
1299      3  0.155519     accept
1299      6  0.560716     accept
...     ...       ...        ...
38        1  0.644427       year
38        2  0.182256       year
38        9  0.173095       year
574      16  0.965214  youve_got
2545      8  0.995250       zone

[1050 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[20, 14, 12, 19, 18, 6, 9, 5, 1, 17, 7, 15, 3, 4, 13, 16, 11, 2, 10, 8])